In [1]:
!pip install faiss-gpu

In [2]:
!pip install pandas-profiling

In [3]:
import faiss

from google.colab import drive
drive.mount('/content/drive')

import numpy as np

import pandas as pd
from pandas_profiling import ProfileReport


from tqdm.notebook import tqdm

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


<ipython-input-3-ba5a3bef1079>:9: DeprecationWarning: `import pandas_profiling` is going to be deprecated by April 1st. Please use `import ydata_profiling` instead.
  from pandas_profiling import ProfileReport


In [4]:
df_base = pd.read_csv('/content/drive/MyDrive/data/base.csv', index_col=0)
df_train = pd.read_csv('/content/drive/MyDrive/data/train.csv', index_col=0)
df_valid = pd.read_csv('/content/drive/MyDrive/data/validation.csv', index_col=0)
df_valid_answ = pd.read_csv('/content/drive/MyDrive/data/validation_answer.csv', index_col=0)

In [5]:
df_base.info()

<class 'pandas.core.frame.DataFrame'>
Index: 2918139 entries, 0-base to 4744766-base
Data columns (total 72 columns):
 #   Column  Dtype  
---  ------  -----  
 0   0       float64
 1   1       float64
 2   2       float64
 3   3       float64
 4   4       float64
 5   5       float64
 6   6       float64
 7   7       float64
 8   8       float64
 9   9       float64
 10  10      float64
 11  11      float64
 12  12      float64
 13  13      float64
 14  14      float64
 15  15      float64
 16  16      float64
 17  17      float64
 18  18      float64
 19  19      float64
 20  20      float64
 21  21      float64
 22  22      float64
 23  23      float64
 24  24      float64
 25  25      float64
 26  26      float64
 27  27      float64
 28  28      float64
 29  29      float64
 30  30      float64
 31  31      float64
 32  32      float64
 33  33      float64
 34  34      float64
 35  35      float64
 36  36      float64
 37  37      float64
 38  38      float64
 39  39      float64


In [6]:
df_base.rename_axis('id').head(2)

0          1         2          3           4          5  \
id                                                                          
0-base -115.083890  11.152912 -64.42676 -118.88089  216.482440 -104.69806   
1-base  -34.562202  13.332763 -69.78761 -166.53348   57.680607  -86.09837   

                 6          7           8          9  ...          62  \
id                                                    ...               
0-base -469.070588  44.348083  120.915344  181.44970  ...  -42.808693   
1-base  -85.076666 -35.637436  119.718636  195.23419  ... -117.767525   

               63         64         65        66         67         68  \
id                                                                        
0-base  38.800827 -151.76218 -74.389090  63.66634  -4.703861   92.93361   
1-base  41.100000 -157.82940 -94.446806  68.20211  24.346846  179.93793   

               69          70         71  
id                                        
0-base  115.26919 -112.756640 -60.830353  
1-base  116.83400  -84.888941 -59.524610  

[2 rows x 72 columns]

In [7]:
df_train.rename(columns=str.lower, inplace=True)
df_train.rename_axis('id').head(2)

0          1          2          3          4         5  \
id                                                                         
0-query -53.882748  17.971436 -42.117104 -183.93668  187.51749 -87.14493   
1-query -87.776370   6.806268 -32.054546 -177.26039  120.80333 -83.81059   

                  6          7          8           9  ...         63  \
id                                                     ...              
0-query -347.360606  38.307602  109.08556   30.413513  ...  70.107360   
1-query  -94.572749 -78.433090  124.91590  140.331070  ...   4.669178   

                64          65         66         67         68         69  \
id                                                                           
0-query -155.80257 -101.965943  65.903790  34.457500  62.642094  134.76360   
1-query -151.69771   -1.638704  68.170876  25.096191  89.974976  130.58963   

                  70         71       target  
id                                            
0-query  -415.750254 -25.958572  675816-base  
1-query -1035.092211 -51.276833  366656-base  

[2 rows x 73 columns]

In [8]:
# Правильные ответы выделяем в отдельную сущность
targets = df_train['target']
df_train.drop('target', axis=1, inplace=True)

In [9]:
df_valid.rename_axis('id').head(2)

0          1          2          3          4  \
id                                                                    
100000-query -57.372734   3.597752 -13.213642 -125.92679  110.74594   
100001-query -53.758705  12.790300 -43.268543 -134.41762  114.44991   

                      5           6           7           8          9  ...  \
id                                                                      ...   
100000-query -81.279594 -461.003172  139.815720  112.880980  75.215750  ...   
100001-query -90.520130 -759.626065   63.995087  127.117905  53.128998  ...   

                    62         63         64         65        66         67  \
id                                                                             
100000-query -75.51302  52.830902 -143.43945  59.051935  69.28224  61.927513   
100001-query -79.44183  29.185436 -168.60590 -82.872443  70.76560 -65.975950   

                     68          69           70         71  
id                                                           
100000-query  111.59253  115.140656 -1099.130485 -117.07936  
100001-query   97.07716  123.391640  -744.442332  -25.00932  

[2 rows x 72 columns]

In [10]:
df_valid_answ.rename(columns=str.lower, inplace=True)
df_valid_answ.rename_axis('id').head(2)

expected
id                        
100000-query  2676668-base
100001-query    91606-base

Построим профайл для df_train:

In [11]:
profile = ProfileReport(df_train, progress_bar=False, minimal=True)
profile

df_train:

В основном признаки имеют нормальное распределение, кроме:  
Признак 6: 20.8% значений = -759, 6.8% значений =-530.   
Признак 21: 64.1% значений = 1507.  
Признак 25: 83.3% значений = 813.   
Признак 33: можно назвать мультимодальным распределением.  
Признак 44: 7.3% значений = -61.  
Признаки 59, 65: равномерное распределение.  
Признак 70: 22.9% значений = -1074.  
  
  
Признаки лежат как в отрицательном диапазоне значений, так и в положительном.   

Преобразуем dataframes в np.arrays:

In [12]:
base = df_base.values.astype('float32')
train = df_train.values.astype('float32')
valid = df_valid.values.astype('float32')

In [ ]:
base.shape[1]

In [13]:
dims = base.shape[1]
n_cells = 1000 # меняем кол-во кластеров
# Сейчас будем бросать вектора размерностью dim 72 и их близость оценивать по Евклидовой норме.
quantizer = faiss.IndexFlatL2(dims)
# Чтобы ускорить процесс используем Inverted File Index, dims=72 измерения, n_cells - кол-во кластеров (групп векторов), их подкручиваем
# "pinecone faiss: the missing manual"
idx_l2 = faiss.IndexIVFFlat(quantizer, dims, n_cells)

In [14]:
# Создание кластеров. Берем полученный индекс idx_l2 (как мы будем хранить данные, саму идею) и ее обучаем.
# Мы забрасываем в индекс несколько векторов. Их получаем из исходного base, берем первые 50000 векторов, функция np.ascontiguousarray делает так,
# чтобы весь массив векторов лежал в оперативной памяти подряд без пропусков. Приводим к float32. Запускаем train.
# В этот момент происходит создание кластеров ()
idx_l2.train(np.ascontiguousarray(base[:50000,:]).astype('float32'))


# Затем все имеющиеся вектора забрасываем в созданные кластеры. Таким образом инициализируем базу данных.
idx_l2.add(np.ascontiguousarray(base).astype('float32'))

# Теперь можно обращаться к БД и говорить "дай мне самые близкие вектора". Вектора лежат без названий, просто под номерами 1, 2, 3.

In [15]:
# Чтобы понимать, что это за вектора, берем названия (из индексов) и нумеруем их подряд.

base_index = {k: v for k, v in enumerate(df_base.index.to_list())}

# del df_base - сделать

In [16]:
# Из всех векторов df_train находим по 5 ближайших соседей. vecs - векторы, idx - их индексы.
vecs, idx = idx_l2.search(np.ascontiguousarray(train).astype('float32'), 5)

In [19]:
preds = {}
for i, neighbors in enumerate(idx):
    preds[i] = [base_index[n] for n in neighbors]

# Вычисляем метрику accuracy@5
acc = 0
for i, (true, predicted) in enumerate(zip(targets, preds.values())):
    if true in predicted:
        acc += 1
print(f'Accuracy@5: {acc/len(train)}')

Accuracy@5: 0.04272


1. Создаем массивы base, train и valid, преобразуя данные из фреймов данных df_base, df_train и df_valid в формат float32.
2. Определяем размерность (dims) массива base.
3. Создаем объект quantizer, используя faiss.IndexFlatL2, которая выполняет быстрый поиск по евклидовой метрике.
4. Создаем индекс idx_l2, используя faiss.IndexIVFFlat с параметрами quantizer, dims и n_cells. Этот индекс разбивает пространство на ячейки для оптимизации поиска.
5. Обучаем индекс idx_l2 на первых 50000 элементах массива base.
6. Создаем словарь base_index, сопоставляющий каждому индексу из массива df_base.index список значений из df_base.index.to_list().
7. Используем индекс idx_l2 для поиска 5 наиболее близких соседей для каждого элемента массива train. Возвращает массив векторов vecs и массив индексов соседей idx.
8. Создаем словарь preds, где каждому элементу массива train соответствует список индексов предсказанных соседей из base.
9. После цикла по всем элементам массива targets вычисляем итоговую точность (accuracy) путем деления счетчика точных совпадений (acc) на общее количество элементов в массиве train. Результат выводим с использованием f-строки в формате "Accuracy@5: {значение точности}".
10. Общий результат работы кода - значение точности (accuracy) в интервале от 0 до 1.

Код выполняет поиск наиболее близких соседей для каждого элемента массива train с использованием индекса idx_l2, и затем вычисляет точность (accuracy) предсказаний путем сравнения соседей с истинными значениями из массива targets.